# Large Event Analysis

In [124]:
import pandas as pd
import numpy as np
import datetime as dt

In [125]:
csv_file = "../datasets/All (1960-2023).csv"
usgs = pd.read_csv(csv_file, sep = ',', lineterminator='\n', dtype={'time':str})
usgs.head()

C:\Users\Vishal\AppData\Local\Temp\ipykernel_16288\2579605054.py:2: DtypeWarning:

Columns (1,2,3,4,6,7,8,9,15,16,17,18) have mixed types. Specify dtype option on import or set low_memory=False.



time    latitude     longitude  depth   mag magType  \
0  2023-10-12T21:41:21.480Z  36.4661674  -120.8755035  15.85  3.15      ml   
1  2023-10-08T21:30:23.900Z  38.8271667      -122.804   1.75  3.87      mw   
2  2023-10-05T03:09:58.000Z      35.041      -117.661   0.79  3.52      ml   
3  2023-10-01T19:29:36.760Z     40.2915     -124.2905   9.59  3.61      mw   
4  2023-10-01T15:41:29.620Z  40.2951667      -124.287    9.8  4.09      mw   

   nst  gap      dmin   rms  ...                   updated  \
0   60  135    0.1035   0.2  ...  2023-10-13T19:19:02.194Z   
1  108   20  0.006058  0.06  ...  2023-10-14T02:06:32.597Z   
2   63   40    0.1102  0.15  ...  2023-10-06T21:24:55.024Z   
3   40  115    0.0308  0.17  ...  2023-10-10T16:43:18.991Z   
4   42  105   0.02685  0.17  ...  2023-10-02T02:34:55.127Z   

                        place        type horizontalError depthError magError  \
0  19 km WNW of New Idria, CA  earthquake             0.4       0.61    0.175   
1  7 km NW of The Geysers, CA  earthquake            0.07       0.11      NaN   
2       5 km NNW of Boron, CA  earthquake            0.12       0.32     0.15   
3      4 km S of Petrolia, CA  earthquake            0.36       0.21      NaN   
4      3 km S of Petrolia, CA  earthquake            0.37       0.23      NaN   

  magNst     status locationSource magSource\r  
0     21  automatic             nc        nc\r  
1      3   reviewed             nc        nc\r  
2    156   reviewed             ci        ci\r  
3      4   reviewed             nc        nc\r  
4      4   reviewed             nc        nc\r  

[5 rows x 22 columns]

In [126]:
#converting the Date column into datetime format
usgs["time"] = pd.to_datetime(usgs["time"], errors="coerce").dt.strftime("%Y-%m-%d")

In [127]:
usgs = usgs[(pd.to_datetime(usgs['time']) > pd.to_datetime('1960-01-01')) & (pd.to_datetime(usgs['time']) < pd.to_datetime('2023-01-01'))]

usgs['longitude'] = pd.to_numeric(usgs['longitude'], errors='coerce')
usgs['latitude'] = pd.to_numeric(usgs['latitude'], errors='coerce')
usgs['mag'] = pd.to_numeric(usgs['mag'], errors='coerce')

#filter the dataset by X > -123 and X < -113 and Y > 29 and Y < 39
usgs = usgs[usgs['longitude'] > -123]
usgs = usgs[usgs['longitude'] < -113]
usgs = usgs[usgs['latitude'] < 39]
usgs = usgs[usgs['latitude'] > 29]

In [128]:
time = []
for i in usgs['time']:
    time.append(pd.to_datetime(i))
usgs['time'] = time

In [129]:
usgs_grouped_counts = pd.DataFrame(usgs.groupby(usgs['time'].dt.to_period('D')).mag.count())
usgs_grouped_counts.rename(columns={'mag':'count'}, inplace=True)

usgs_grouped_max = pd.DataFrame(usgs.groupby(usgs['time'].dt.to_period('D')).mag.max())

In [130]:
import plotly.express as px
import plotly.graph_objects as go

Number of Earthquakes generated by USGS

In [131]:
usgs_grouped_counts.reset_index(inplace=True)
usgs_grouped_counts['time'] = usgs_grouped_counts['time'].dt.to_timestamp()

fig = px.line(usgs_grouped_counts, x='time', 
              y='count', labels={'value': 'Magnitude'}, 
              title='USGS Earthquake Counts By Day')
fig.update_layout(
    width=1000,
    height=600,
)

fig.update_traces(line=dict(width=1.0))
fig.update_xaxes(rangeslider_visible=True)
fig.update_layout(dragmode='pan')

fig.show()

Maximum magnitude of earthquakes generated each day by ETAS

In [132]:
usgs_grouped_max.reset_index(inplace=True)
usgs_grouped_max['time'] = usgs_grouped_max['time'].dt.to_timestamp()

fig = px.line(usgs_grouped_max, x='time', 
              y='mag', labels={'value': 'Magnitude'}, 
              title='USGS Earthquake Max By Day')
fig.update_layout(
    width=1000,
    height=600,
)

fig.update_traces(line=dict(width=1.0))
fig.update_xaxes(rangeslider_visible=True)
fig.update_layout(dragmode='pan')

fig.show()

In [133]:
#filter usgs_grouped_counts to the 10 largest values
usgs_grouped_counts_top10 = usgs_grouped_counts.nlargest(10, 'count')
usgs_grouped_counts_top10.head(10)


time  count
10743 2019-07-06    605
9330  2010-04-05    233
6007  1992-06-28    226
3155  1979-10-16    189
6008  1992-06-29    186
7561  1999-10-16    181
6387  1994-01-17    148
4000  1983-05-03    147
1377  1971-02-09    145
3298  1980-05-26    139

In [134]:
#filter the usgs_grouped_max to the 10 largest values 
usgs_grouped_max_top10 = usgs_grouped_max.nlargest(10, 'mag')
usgs_grouped_max_top10.head(10)

time  mag
6007  1992-06-28  7.3
9329  2010-04-04  7.2
7561  1999-10-16  7.1
10743 2019-07-06  7.1
5466  1989-10-18  6.9
3999  1983-05-02  6.7
6387  1994-01-17  6.7
939   1968-04-09  6.6
1377  1971-02-09  6.6
5040  1987-11-24  6.6

In [135]:
one_week = dt.timedelta(days=7)
usgs_grouped_counts_top10 = usgs_grouped_counts_top10.sort_values(by='time', ascending=True)
usgs_grouped_max_top10 = usgs_grouped_counts_top10.sort_values(by='time', ascending=True)


In [136]:
filtered_data_df = pd.DataFrame()

# Plotting 1 week before/after a day of high count of earthquakes
for index, row in usgs_grouped_counts_top10.iterrows():
    current_time = row['time']
    previous_time = current_time - one_week
    next_time = current_time + one_week
    
    filtered_data_before = usgs_grouped_counts[(usgs_grouped_counts['time'] >= previous_time) & (usgs_grouped_counts['time'] < current_time)].copy()
    filtered_data_before['days_until_large_value'] = (current_time - filtered_data_before['time']).dt.days  # Calculate days until the large value
    
    filtered_data_after = usgs_grouped_counts[(usgs_grouped_counts['time'] <= next_time) & (usgs_grouped_counts['time'] >= current_time)].copy()
    filtered_data_after['days_until_large_value'] = (current_time - filtered_data_after['time']).dt.days  # Calculate days until the large value
    
    filtered_data_df = pd.concat([filtered_data_df, filtered_data_before, filtered_data_after])

In [137]:
fig = go.Figure()

scatter = go.Scatter(
    x=filtered_data_df['days_until_large_value'],
    y=filtered_data_df['count'],
    mode='markers',
    marker=dict(
        size= 6,
        color=filtered_data_df['count'],
        colorscale='Viridis',
        colorbar=dict(title='Number of Earthquakes'),
    ),
    text=filtered_data_df['time'],
)

fig.add_trace(scatter)

fig.update_layout(
    title='Top 10 Highest Earthquake Counts, 1 Week Before/After',
    xaxis=dict(title='Days Until Large Value'),
    yaxis=dict(title='Number of Earthquakes'),
    width=1000,
    height=600,
)

fig.update_xaxes(title_text='Days Before/After Spike')
fig.update_xaxes(rangeslider_visible=True)
fig.update_layout(dragmode='pan')

fig.show()

write description about this

In [138]:
filtered_data_df = pd.DataFrame()

# Plotting 1 week before/after a large earthquake
for index, row in usgs_grouped_max_top10.iterrows():
    current_time = row['time']
    previous_time = current_time - one_week
    next_time = current_time + one_week
    
    filtered_data_before = usgs_grouped_max[(usgs_grouped_max['time'] >= previous_time) & (usgs_grouped_max['time'] < current_time)].copy()
    filtered_data_before['days_until_large_value'] = (current_time - filtered_data_before['time']).dt.days  # Calculate days until the large value
    
    filtered_data_after = usgs_grouped_max[(usgs_grouped_max['time'] <= next_time) & (usgs_grouped_max['time'] >= current_time)].copy()
    filtered_data_after['days_until_large_value'] = (current_time - filtered_data_after['time']).dt.days  # Calculate days until the large value
    
    filtered_data_df = pd.concat([filtered_data_df, filtered_data_before, filtered_data_after])

In [139]:
fig = go.Figure()

scatter = go.Scatter(
    x=filtered_data_df['days_until_large_value'],
    y=filtered_data_df['mag'],
    mode='markers',
    marker=dict(
        size=6, 
        color=filtered_data_df['mag'],
        colorscale='Viridis',
        colorbar=dict(title='Magnitude'),
    ),
    text=filtered_data_df['time'],
)

fig.add_trace(scatter)

fig.update_layout(
    title='Top 10 Largest Earthquakes, 1 Week Before/After',
    xaxis=dict(title='Days Before/After Spike'),
    yaxis=dict(title='Magnitude'),
    width=1000,
    height=600,
)

fig.update_xaxes(rangeslider_visible=True)
fig.update_layout(dragmode='pan')

fig.show()

write description about this

In [140]:
filtered_data_df = pd.DataFrame()

# Plotting locations of earthquakes 1 week before/after a day of high count of earthquakes
for index, row in usgs_grouped_counts_top10.iterrows():
    current_time = row['time']
    previous_time = current_time - one_week
    next_time = current_time + one_week
    
    filtered_data_before = usgs[(usgs['time'] >= previous_time) & (usgs['time'] < current_time)].copy()
    filtered_data_before['days_until_large_value'] = (current_time - filtered_data_before['time']).dt.days
    
    filtered_data_after = usgs[(usgs['time'] <= next_time) & (usgs['time'] >= current_time)].copy()
    filtered_data_after['days_until_large_value'] = (current_time - filtered_data_after['time']).dt.days
    
    # Add a new column 'time_group' to identify different times for symbols
    filtered_data_before['time_group'] = str(current_time)
    filtered_data_after['time_group'] = str(current_time)
    
    filtered_data_df = pd.concat([filtered_data_df, filtered_data_before, filtered_data_after])


Lets look at the location of earthquakes during spikes

In [141]:
fig = go.Figure()

color_scale_min = -6
color_scale_max = 6

for time_group in filtered_data_df['time_group'].unique():
    subset_df = filtered_data_df[filtered_data_df['time_group'] == time_group]
    
    fig.add_trace(go.Scatter(
        x=subset_df['longitude'],
        y=subset_df['latitude'],
        mode='markers',
        marker=dict(
            size=subset_df['mag'],
            sizemode='diameter',
            sizeref=0.4,
            color=subset_df['days_until_large_value'],
            symbol='circle',
            colorbar=dict(
                tickfont=dict(
                    size=12
                ),
                x=0.5,
                y=-0.2,
                orientation='h',
                len=1.0,
                title='Days +/- Large Event',
            ),
            showscale=True,
            colorscale='Viridis',
            cmin = color_scale_min,
            cmax = color_scale_max
        ),
        text=subset_df['time'],
        name=str(time_group)
    ))

# Update layout
fig.update_layout(
    width=800,
    height=800,
    title='Earthquake Locations Before/After Large Count Of Earthquakes',
    xaxis=dict(title='Longitude'),
    yaxis=dict(title='Latitude'),
    dragmode='pan',
    legend=dict(
        title='Time Groups',
        font=dict(
            size=12
        ),
    ),
)

fig.show()

In [142]:
filtered_data_df = pd.DataFrame()

# Plotting locations of earthquakes 1 week before/after a large  earthquake
for index, row in usgs_grouped_max_top10.iterrows():
    current_time = row['time']
    previous_time = current_time - one_week
    next_time = current_time + one_week
    
    filtered_data_before = usgs[(usgs['time'] >= previous_time) & (usgs['time'] < current_time)].copy()
    filtered_data_before['days_until_large_value'] = (current_time - filtered_data_before['time']).dt.days
    
    filtered_data_after = usgs[(usgs['time'] <= next_time) & (usgs['time'] >= current_time)].copy()
    filtered_data_after['days_until_large_value'] = (current_time - filtered_data_after['time']).dt.days
    
    # Add a new column 'time_group' to identify different times for symbols
    filtered_data_before['time_group'] = str(current_time)
    filtered_data_after['time_group'] = str(current_time)
    
    filtered_data_df = pd.concat([filtered_data_df, filtered_data_before, filtered_data_after])

In [143]:
fig = go.Figure()

color_scale_min = -6
color_scale_max = 6

for time_group in filtered_data_df['time_group'].unique():
    subset_df = filtered_data_df[filtered_data_df['time_group'] == time_group]
    
    fig.add_trace(go.Scatter(
        x=subset_df['longitude'],
        y=subset_df['latitude'],
        mode='markers',
        marker=dict(
            size=subset_df['mag'],
            sizemode='diameter',
            sizeref=0.4,
            color=subset_df['days_until_large_value'],
            symbol='circle',
            colorbar=dict(
                tickfont=dict(
                    size=12
                ),
                x=0.5,
                y=-0.2,
                orientation='h',
                len=1.0,
                title='Days +/- Large Event',
            ),
            showscale=True,
            colorscale='Viridis',
            cmin = color_scale_min,
            cmax = color_scale_max
        ),
        text=subset_df['time'],
        name=str(time_group)
    ))

# Update layout
fig.update_layout(
    width=800,
    height=800,
    title='Earthquake Locations Before/After Large Earthquake',
    xaxis=dict(title='Longitude'),
    yaxis=dict(title='Latitude'),
    dragmode='pan',
    legend=dict(
        title='Time Groups',
        font=dict(
            size=12
        ),
    ),
)

# Show the interactive plot
fig.show()

Lets take a look at the energy before a large number of earthquakes

In [144]:
csv_file = "../datasets/All (1960-2023).csv"
usgs_energy = pd.read_csv(csv_file, sep = ',', lineterminator='\n', dtype={'time':str})
usgs_energy["time"] = pd.to_datetime(usgs_energy["time"], errors="coerce")
usgs_energy['mag'] = pd.to_numeric(usgs_energy['mag'], errors='coerce')
usgs_energy.head()

C:\Users\Vishal\AppData\Local\Temp\ipykernel_16288\741639755.py:2: DtypeWarning:

Columns (1,2,3,4,6,7,8,9,15,16,17,18) have mixed types. Specify dtype option on import or set low_memory=False.



time    latitude     longitude  depth   mag  \
0 2023-10-12 21:41:21.480000+00:00  36.4661674  -120.8755035  15.85  3.15   
1 2023-10-08 21:30:23.900000+00:00  38.8271667      -122.804   1.75  3.87   
2        2023-10-05 03:09:58+00:00      35.041      -117.661   0.79  3.52   
3 2023-10-01 19:29:36.760000+00:00     40.2915     -124.2905   9.59  3.61   
4 2023-10-01 15:41:29.620000+00:00  40.2951667      -124.287    9.8  4.09   

  magType  nst  gap      dmin   rms  ...                   updated  \
0      ml   60  135    0.1035   0.2  ...  2023-10-13T19:19:02.194Z   
1      mw  108   20  0.006058  0.06  ...  2023-10-14T02:06:32.597Z   
2      ml   63   40    0.1102  0.15  ...  2023-10-06T21:24:55.024Z   
3      mw   40  115    0.0308  0.17  ...  2023-10-10T16:43:18.991Z   
4      mw   42  105   0.02685  0.17  ...  2023-10-02T02:34:55.127Z   

                        place        type horizontalError depthError magError  \
0  19 km WNW of New Idria, CA  earthquake             0.4       0.61    0.175   
1  7 km NW of The Geysers, CA  earthquake            0.07       0.11      NaN   
2       5 km NNW of Boron, CA  earthquake            0.12       0.32     0.15   
3      4 km S of Petrolia, CA  earthquake            0.36       0.21      NaN   
4      3 km S of Petrolia, CA  earthquake            0.37       0.23      NaN   

  magNst     status locationSource magSource\r  
0     21  automatic             nc        nc\r  
1      3   reviewed             nc        nc\r  
2    156   reviewed             ci        ci\r  
3      4   reviewed             nc        nc\r  
4      4   reviewed             nc        nc\r  

[5 rows x 22 columns]

In [145]:
usgs_energy = usgs_energy[(usgs_energy['time'] > '1960-01-01') & (usgs_energy['time'] < '2023-01-01')]

usgs_energy['longitude'] = pd.to_numeric(usgs_energy['longitude'], errors='coerce')
usgs_energy['latitude'] = pd.to_numeric(usgs_energy['latitude'], errors='coerce')

#filter the dataset by X > -123 and X < -113 and Y > 29 and Y < 39
usgs_energy = usgs_energy[usgs_energy['longitude'] > -123]
usgs_energy = usgs_energy[usgs_energy['longitude'] < -113]
usgs_energy = usgs_energy[usgs_energy['latitude'] < 39]
usgs_energy = usgs_energy[usgs_energy['latitude'] > 29]

usgs_energy.head()

time   latitude   longitude depth   mag  \
240 2022-12-31 12:12:26.650000+00:00  33.397500 -116.393333  3.88  4.14   
241 2022-12-31 11:41:09.460000+00:00  34.355667 -116.921833  4.73  3.47   
246 2022-12-22 02:22:50.250000+00:00  37.620167 -122.025000  3.82  3.34   
262 2022-12-17 11:39:42.860000+00:00  37.918167 -122.304000  5.48  3.57   
263 2022-12-13 12:31:28.820000+00:00  36.604667 -121.209333  8.88  3.28   

    magType  nst gap     dmin   rms  ...                   updated  \
240      mw  132  16  0.07391  0.19  ...  2023-09-22T21:50:30.029Z   
241      mw  121  25  0.07845  0.15  ...  2023-03-07T19:00:01.040Z   
246      mw  141  16      NaN  0.16  ...  2023-04-20T04:34:00.806Z   
262      mw  170  19  0.01598  0.15  ...  2023-07-27T08:15:34.318Z   
263      ml   67  55  0.03812  0.09  ...  2023-02-18T22:04:08.040Z   

                              place        type horizontalError depthError  \
240  16 km N of Borrego Springs, CA  earthquake             0.1       0.38   
241  11km SSE of Lucerne Valley, CA  earthquake            0.09       0.41   
246         3km N of Union City, CA  earthquake             0.1       0.17   
262       1km ENE of El Cerrito, CA  earthquake             0.1       0.17   
263        10km NW of Pinnacles, CA  earthquake            0.14       0.28   

    magError magNst    status locationSource magSource\r  
240      NaN      6  reviewed             ci        ci\r  
241      NaN      4  reviewed             ci        ci\r  
246      NaN      3  reviewed             nc        nc\r  
262      NaN      4  reviewed             nc        nc\r  
263    0.129     72  reviewed             nc        nc\r  

[5 rows x 22 columns]

In [146]:
formula_constant = (1/1.5)
usgs_energy['energy'] = 10**(1.5*usgs_energy['mag'])
usgs_energy['energy'] = np.log(usgs_energy['energy']) * formula_constant
usgs_energy.head()

time   latitude   longitude depth   mag  \
240 2022-12-31 12:12:26.650000+00:00  33.397500 -116.393333  3.88  4.14   
241 2022-12-31 11:41:09.460000+00:00  34.355667 -116.921833  4.73  3.47   
246 2022-12-22 02:22:50.250000+00:00  37.620167 -122.025000  3.82  3.34   
262 2022-12-17 11:39:42.860000+00:00  37.918167 -122.304000  5.48  3.57   
263 2022-12-13 12:31:28.820000+00:00  36.604667 -121.209333  8.88  3.28   

    magType  nst gap     dmin   rms  ...                           place  \
240      mw  132  16  0.07391  0.19  ...  16 km N of Borrego Springs, CA   
241      mw  121  25  0.07845  0.15  ...  11km SSE of Lucerne Valley, CA   
246      mw  141  16      NaN  0.16  ...         3km N of Union City, CA   
262      mw  170  19  0.01598  0.15  ...       1km ENE of El Cerrito, CA   
263      ml   67  55  0.03812  0.09  ...        10km NW of Pinnacles, CA   

           type horizontalError depthError magError magNst    status  \
240  earthquake             0.1       0.38      NaN      6  reviewed   
241  earthquake            0.09       0.41      NaN      4  reviewed   
246  earthquake             0.1       0.17      NaN      3  reviewed   
262  earthquake             0.1       0.17      NaN      4  reviewed   
263  earthquake            0.14       0.28    0.129     72  reviewed   

    locationSource magSource\r    energy  
240             ci        ci\r  9.532702  
241             ci        ci\r  7.989970  
246             nc        nc\r  7.690634  
262             nc        nc\r  8.220229  
263             nc        nc\r  7.552479  

[5 rows x 23 columns]

In [147]:
from datetime import datetime

In [148]:
usgs_energy['time'] = pd.to_datetime(usgs_energy['time']).dt.strftime("%Y-%m-%d %H:%M:%S.%f%z")
usgs_energy['time'] = usgs_energy['time'].apply(lambda x: datetime.strptime(x, "%Y-%m-%d %H:%M:%S.%f%z"))
usgs_energy.head()

time   latitude   longitude depth   mag  \
240 2022-12-31 12:12:26.650000+00:00  33.397500 -116.393333  3.88  4.14   
241 2022-12-31 11:41:09.460000+00:00  34.355667 -116.921833  4.73  3.47   
246 2022-12-22 02:22:50.250000+00:00  37.620167 -122.025000  3.82  3.34   
262 2022-12-17 11:39:42.860000+00:00  37.918167 -122.304000  5.48  3.57   
263 2022-12-13 12:31:28.820000+00:00  36.604667 -121.209333  8.88  3.28   

    magType  nst gap     dmin   rms  ...                           place  \
240      mw  132  16  0.07391  0.19  ...  16 km N of Borrego Springs, CA   
241      mw  121  25  0.07845  0.15  ...  11km SSE of Lucerne Valley, CA   
246      mw  141  16      NaN  0.16  ...         3km N of Union City, CA   
262      mw  170  19  0.01598  0.15  ...       1km ENE of El Cerrito, CA   
263      ml   67  55  0.03812  0.09  ...        10km NW of Pinnacles, CA   

           type horizontalError depthError magError magNst    status  \
240  earthquake             0.1       0.38      NaN      6  reviewed   
241  earthquake            0.09       0.41      NaN      4  reviewed   
246  earthquake             0.1       0.17      NaN      3  reviewed   
262  earthquake             0.1       0.17      NaN      4  reviewed   
263  earthquake            0.14       0.28    0.129     72  reviewed   

    locationSource magSource\r    energy  
240             ci        ci\r  9.532702  
241             ci        ci\r  7.989970  
246             nc        nc\r  7.690634  
262             nc        nc\r  8.220229  
263             nc        nc\r  7.552479  

[5 rows x 23 columns]

In [149]:
usgs_grouped_energy = pd.DataFrame(usgs_energy.groupby(usgs_energy['time'].dt.to_period('S')).energy.sum())
usgs_grouped_energy.reset_index(inplace=True)
usgs_grouped_energy.head()

c:\Users\Vishal\AppData\Local\Programs\Python\Python310\lib\site-packages\pandas\core\arrays\datetimes.py:1162: UserWarning:

Converting to PeriodArray/Index representation will drop timezone information.



time    energy
0  1960-01-02 22:51:45  9.302444
1  1960-01-05 18:01:47  6.976833
2  1960-01-07 17:51:32  8.381410
3  1960-01-08 06:51:21  7.138014
4  1960-01-11 19:08:39  8.726798

In [150]:
usgs_grouped_energy['time'] = usgs_grouped_energy['time'].dt.to_timestamp()

fig = px.line(usgs_grouped_energy, x='time', 
              y='energy', labels={'value': 'energy'}, 
              title='USGS Energy')
fig.update_layout(
    width=1000,
    height=600,
)

fig.update_traces(line=dict(width=1.0))
fig.update_xaxes(rangeslider_visible=True)
fig.update_layout(dragmode='pan')

fig.show()

In [151]:
filtered_data_df = pd.DataFrame()

# Plotting 1 week before/after a day with a large number of earthquakes
for index, row in usgs_grouped_counts_top10.iterrows():
    current_time = row['time']
    previous_time = current_time - one_week
    next_time = current_time + one_week
    
    filtered_data_before = usgs_grouped_energy[(usgs_grouped_energy['time'] >= previous_time) & (usgs_grouped_energy['time'] < current_time)].copy()
    filtered_data_before['time_until_large_value'] = (current_time - filtered_data_before['time'])
    
    filtered_data_after = usgs_grouped_energy[(usgs_grouped_energy['time'] <= next_time) & (usgs_grouped_energy['time'] >= current_time)].copy()
    filtered_data_after['time_until_large_value'] = (current_time - filtered_data_after['time'])
    
    filtered_data_df = pd.concat([filtered_data_df, filtered_data_before, filtered_data_after])


In [152]:
fig = go.Figure()

scatter = go.Scatter(
    x=filtered_data_df['time_until_large_value'],
    y=filtered_data_df['energy'],
    mode='markers',
    marker=dict(
        size=6,
        color=filtered_data_df['energy'],
        colorscale='Viridis',
        colorbar=dict(title='Energy'),
    ),
    text=filtered_data_df['time'],
)

fig.add_trace(scatter)

fig.update_layout(
    title='Top 10 Largest Earthquake Count Days, 1 Week Before/After (Energy)',
    xaxis=dict(title='Days Before/After Spike'),
    yaxis=dict(title='Energy'),
    width=1000,
    height=600,
)

# Add interactivity
fig.update_xaxes(rangeslider_visible=True)
fig.update_layout(dragmode='pan')

fig.show()